# Bank Dataset: EDA

In [105]:
# pip install plotly

In [58]:
import numpy as np
import pandas as pd

import os
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

import sys
import warnings
if not sys.warnoptions:
    warnings.simplefilter('ignore')

## Functions

In [88]:
def plot_bars(colname, title):
    fig = go.Figure()
    fig.add_trace(go.Bar(x=df_yes[colname].value_counts(normalize=True).index,
                         y=df_yes[colname].value_counts(normalize=True).values,
                         marker_color='darkslateblue', opacity=.7, 
                         name='Target: Yes'))
    fig.add_trace(go.Bar(x=df_no[colname].value_counts(normalize=True).index,
                         y=df_no[colname].value_counts(normalize=True).values,
                         marker_color='indianred', opacity=.7, 
                         name='Target: No'))
    fig.update_layout(barmode='group', title=f'{title}', titlefont={'size': 20},
                      legend={'orientation': 'h', 'y': 1, 'yanchor': 'bottom'},
                      yaxis_tickformat='.0%')
    fig.show()

In [89]:
def plot_boxes(colname, yaxis):

    perc_99 = df[colname].quantile(.99)

    fig = go.Figure()
    fig.add_trace(go.Box(y=df_yes[df_yes[colname].lt(perc_99)][colname], 
                         marker_color='darkslateblue', 
                         name='Target: Yes'))
    fig.add_trace(go.Box(y=df_no[df_no[colname].lt(perc_99)][colname], 
                         marker_color='indianred', 
                         name='Target: No'))
    fig.update_layout(title=f'{colname.title()}', titlefont={'size': 20},
                      legend={'orientation': 'h', 'y': 1, 'yanchor': 'bottom'},
                      yaxis_title=yaxis
                      )
    fig.show()

## Loading Data

In [90]:
explain_dict = {
    'age': 'Age',
    'job': 'Job',
    'marital': 'Marital status',
    'education': 'Education',
    'default': 'Defaulted on previous loan',
    'balance': 'Yearly balace (€)',
    'housing': 'Has mortgage',
    'loan': 'Has personal loan',
    'contact': "Means of contact",
    'day': 'Day of last contact',
    'month': 'Month of last contact',
    'duration': 'Last contact duration (seconds)',
    'campaign': 'Number of contacts during this campaign',
    'pdays': 'Days since last contact',
    'previous': 'Number of previous campaigns',
    'poutcome': 'Previous campaign outcome',
}

In [91]:
# <!--   1 - age (numeric)
  
#    2 - job : type of job
   
#    3 - marital : marital status
   
#    4 - education (categorical: "unknown","secondary","primary","tertiary")
   
#    5 - default: has credit in default? (binary: "yes","no")
   
#    6 - balance: average yearly balance, in euros (numeric) 
   
#    7 - housing: has housing loan? (binary: "yes","no")
   
#    8 - loan: has personal loan? (binary: "yes","no")
   
#    9 - contact: contact communication type (categorical: "unknown","telephone","cellular") 
   
#   10 - day: last contact day of the month (numeric)
  
#   11 - month: last contact month of year (categorical: "jan", "feb", "mar", ..., "nov", "dec")
  
#   12 - duration: last contact duration, in seconds (numeric)
  
#   13 - campaign: number of contacts performed during this campaign and for this client (numeric, includes last contact)
  
#   14 - pdays: number of days that passed by after the client was last contacted from a previous campaign (numeric, -1 means client was not previously contacted)
  
#   15 - previous: number of contacts performed before this campaign and for this client (numeric)
  
#   16 - poutcome: outcome of the previous marketing campaign -->

In [92]:
df = pd.read_csv('bank-full.csv', sep=';')
df.head()

age           job  marital  education default  balance housing loan  \
0   58    management  married   tertiary      no     2143     yes   no   
1   44    technician   single  secondary      no       29     yes   no   
2   33  entrepreneur  married  secondary      no        2     yes  yes   
3   47   blue-collar  married    unknown      no     1506     yes   no   
4   33       unknown   single    unknown      no        1      no   no   

   contact  day month  duration  campaign  pdays  previous poutcome   y  
0  unknown    5   may       261         1     -1         0  unknown  no  
1  unknown    5   may       151         1     -1         0  unknown  no  
2  unknown    5   may        76         1     -1         0  unknown  no  
3  unknown    5   may        92         1     -1         0  unknown  no  
4  unknown    5   may       198         1     -1         0  unknown  no

In [93]:
df.shape

(45211, 17)

In [94]:
# no missing values

df.isnull().sum()

age          0
job          0
marital      0
education    0
default      0
balance      0
housing      0
loan         0
contact      0
day          0
month        0
duration     0
campaign     0
pdays        0
previous     0
poutcome     0
y            0
dtype: int64

In [95]:
# no duplicates

df.duplicated().sum()

0

In [96]:
assert df.index.is_monotonic

## Target Variable Distribution

In [97]:
df['y'].value_counts(dropna=False, normalize=True)

no     0.883015
yes    0.116985
Name: y, dtype: float64

## Correlations

In [98]:
df['y_numeric'] = df['y'].replace({'no': 0, 'yes': 1})

In [99]:
# features previous & pdays are correlated
# slight correlation between target value and duration of the previous conversation

df.corr().style.background_gradient(cmap='Blues').format('{:,.2f}')

## Object columns

In [100]:
df_yes, df_no = df[df['y'] == 'yes'], df[df['y'] == 'no']

In [101]:
object_cols = df.select_dtypes(include='object').columns[:-1]
object_cols

for col in object_cols:
    plot_bars(col, explain_dict[col])

## Numeric Columns

In [102]:
number_cols = df.select_dtypes(exclude='object').columns[:-1].tolist()
number_cols.remove('day')

for col in number_cols:
    plot_boxes(col, explain_dict[col])

In [78]:
df.columns

Index(['age', 'job', 'marital', 'education', 'default', 'balance', 'housing',
       'loan', 'contact', 'day', 'month', 'duration', 'campaign', 'pdays',
       'previous', 'poutcome', 'y', 'y_numeric'],
      dtype='object')

## Conclusions

- Imbalanced dataset (88% no / 12% yes). Meaning, **accuracy is a bad metric**, we need to use something balanced (e.g. F1 or ROC AUC score).
- 2 correlated features: previous (number of previous campaigns) and pdays (days since last contact). Correlation is positive, not strong.
- **Duration of last contact** correlated with target, might be a case of data leakage (i.e. customer agreed to the new product >>> longer call to sign them up).
- On average, people who agree to the new product are:
    - have higher yearly balance
    - were contacted less during the current campaign
    - have more days since last contact. This has values -1 (never contacted?)
    - have been in more campaigns before
    - are single / divorced more often than customers who didn't agree
    - are less likely to have mortgage (large loans), but more likely to have other personal loans (smaller loans), so maybe lower financial literacy